In [1]:
!pip install backtesting

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.5/175.5 kB 1.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for backtesting: filename=Backtesting-0.3.3-py3-none-any.whl size=173916 sha256=0e24f41c439e01aa25b96724e04338f1b6b00f136559b6c47fc4c8f52da7166c
  Stored in directory: /root/.cache/pip/wheels/e2/30/7f/19cbe31987c6ebdb47f1f510343249066711609e3da2d57176
Successfully built backtesting


In [2]:
!pip install ta

  Preparing metadata (setup.py) ... done
  Created wheel for ta: filename=ta-0.11.0-py3-none-any.whl size=29411 sha256=7416d2a2411e7c152bea44ed0cff115ddec56b2f0a1f3a006f87ef62f669183e
  Stored in directory: /root/.cache/pip/wheels/5f/67/4f/8a9f252836e053e532c6587a3230bc72a4deb16b03a829610b
Successfully built ta


In [3]:
import pandas as pd
import numpy as np
import math
import matplotlib.pyplot as plt
import statistics
from IPython.display import clear_output
import time
import datetime
from mpl_toolkits import mplot3d
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

from ta import add_all_ta_features
from ta.utils import dropna

In [4]:
class price_sim:

  """
    A Python class for simulating and analyzing financial price data using Geometric Brownian Motion (GBM).

    This class provides a set of functions to load historical price data, calculate returns, simulate GBM,
    and visualize the results. It includes functionalities for both regular simulation and backtesting.

    Attributes:
        - ticker (str): Ticker symbol for the financial instrument.
        - start_date (list): Start date [year, month, day] for historical data loading.
        - end_date (list/str): End date [year, month, day] or 'today' for historical data loading.
        - interval (str): Data interval (e.g., '1d') for historical data loading.
        - predicted_period (int): Number of periods for future price simulation.
        - backtesting (bool): True for backtesting, False for regular simulation.

    Functions:
        - data_loading: Compiles historical price data from Yahoo Finance for a specified ticker.
        - returnify: Calculates simple returns for provided financial data.
        - log_returnify: Calculates log returns for provided financial data.
        - GBM_params: Calculates mean and standard deviation of returns.
        - GBM: Simulates Geometric Brownian Motion for a given set of parameters.
        - plot_paths: Plots realizations of GBM along with actual exchange rates.
        - plot_paths_on_profit_space: Plots realizations of GBM with profit space boundaries.
        - pipeline: Executes the complete pipeline for GBM simulation and visualization.

    Note:
        - The class assumes the use of Pandas for handling financial data and NumPy for numerical operations.
        - Visualization functionalities use Matplotlib for plotting.
  """

  def data_loading(self, ticker, start_date, end_date, interval):

      """
      - Calculates log returns for the provided financial data.

    - Parameters:
          - FX_data (Pandas DataFrame): Financial data.
          - date_col (str, optional): Column containing dates.

      - Returns:
        - Pandas DataFrame with dates and corresponding log returns.
      """

      self.ticker = ticker
      self.start_date = start_date
      self.end_date = end_date
      self.interval = interval

      yh_start_date = int(time.mktime(datetime.datetime(self.start_date[0], self.start_date[1], self.start_date[2], 23, 59).timetuple()))

      if self.end_date == 'today':
        yh_end_date = int(time.mktime(datetime.datetime.now().timetuple()))
      else:
        yh_end_date = int(time.mktime(datetime.datetime(self.end_date[0], self.end_date[1], self.end_date[2], 23, 59).timetuple()))

      query_string1 = f'https://query1.finance.yahoo.com/v7/finance/download/{ticker}?period1={yh_start_date}&period2={yh_end_date}&interval={self.interval}&events=history&includeAdjustedClose=true'

      FX_data = pd.read_csv(query_string1)
      FX_data['Adj Close'] = FX_data['Adj Close']

      return FX_data

  def returnify(self, FX_data, date_col = None):

      """
      - Calculates simple returns for the provided financial data.

     - Parameters:
          - FX_data (Pandas DataFrame): Financial data.
          - date_col (str, optional): Column containing dates.

      - Returns:
          - Pandas DataFrame with dates and corresponding returns.
      """

      self.FX_data = FX_data
      self.date_col = date_col

      if self.date_col != None:
        prices = self.FX_data.loc[:, self.FX_data.columns != self.date_col]
        dates = self.FX_data[date_col]
        returns = prices / prices.shift(1) - 1
        returnified = pd.concat([dates, returns], axis = 1,)

      else:
        prices = self.FX_data
        returns = prices / prices.shift(1) - 1
        returnified = returns

      return returnified

  def log_returnify(self, FX_data, date_col = None):

      """
    - Calculates log returns for the provided financial data.

    - Parameters:
        - FX_data (Pandas DataFrame): Financial data.
        - date_col (str, optional): Column containing dates.

    - Returns:
        - Pandas DataFrame with dates and corresponding log returns.
      """

      self.FX_data = FX_data
      self.date_col = date_col

      if self.date_col != None:
        prices = self.FX_data.loc[:, self.FX_data.columns != self.date_col]
        dates = self.FX_data[self.date_col]
        returns = np.log(prices) - np.log(prices.shift(1))
        returnified = pd.concat([dates, returns], axis = 1,)

      else:
        prices = self.FX_data
        returns = np.log(prices) - np.log(prices.shift(1))
        returnified = returns

      return returnified

  def streak_logic(self, last_streak, t0_value, tm1_value):

      if ((t0_value > 0) and (tm1_value >0)) or ((t0_value < 0) and (tm1_value < 0)):
        last_streak +=1
      elif ((t0_value > 0) and (tm1_value < 0)) or ((t0_value < 0) and (tm1_value > 0)):
        last_streak = 1
      elif t0_value == 0:
        last_streak = last_streak

      return last_streak

  def streak_counter(self, pd_series):
      streak = 0
      streak_series = pd.Series(1)

      for i in range(1, len(pd_series)):
        t0_value = pd_series[i]
        tm1_value = pd_series[i-1]

        streak = self.streak_logic(streak, t0_value, tm1_value)

        streak_series = pd.concat([streak_series, pd.Series(streak)], axis = 1, ignore_index= True)

      return streak_series

  def GBM_params(self, returns):

      """
    - Calculates the mean (mu) and standard deviation (sigma) of returns.

    - Parameters:
        - returns (Pandas Series): Financial returns.

    - Returns:
        - Tuple (mu, sigma) representing mean and standard deviation.
      """

      self.returns = returns

      mu = self.returns.describe().at['mean']
      sigma = self.returns.describe().at['std']

      return mu, sigma

  def GBM(self, mu, sigma, S0, steps, n_paths, plot = 'N', pandas = 'Y'):

      """
    - Simulates Geometric Brownian Motion (GBM) for a given set of parameters.

    - Parameters:
        - mu (float): Mean of returns.
        - sigma (float): Standard deviation of returns.
        - S0 (float): Initial stock price.
        - steps (int): Number of time steps.
        - n_paths (int): Number of simulation paths.
        - plot (str): 'Y' to plot simulation, 'N' otherwise.
        - pandas (str): 'Y' to return Pandas DataFrame, 'N' for NumPy array.

    - Returns:
        - Pandas DataFrame or NumPy array representing GBM simulation.
      """

      self.mu = mu
      self.sigma = sigma
      self.S0 = S0
      self.steps = steps
      self.n_paths = n_paths
      self.plot = plot
      self.pandas = pandas

      T = 1

      # calc each time step
      dt = T/self.steps

      # simulation using numpy arrays
      St = np.exp(
          (self.mu - self.sigma ** 2 / 2) * dt
          + self.sigma * np.random.normal(0, np.sqrt(dt), size=(self.n_paths,self.steps)).T
      )

      # include array of 1's
      St = np.vstack([np.ones(self.n_paths), St])

      # multiply through by S0 and return the cumulative product of elements along a given simulation path (axis=0).
      St = self.S0 * St.cumprod(axis=0)

      if self.plot == 'Y':
        # Define time interval correctly
        time = np.linspace(0,T,self.steps+1)

        # Require numpy array that is the same shape as St
        tt = np.full(shape=(self.n_paths,self.steps+1), fill_value=time).T

        plt.plot(tt, St)
        plt.xlabel("Years $(t)$")
        plt.ylabel("Stock Price $(S_t)$")
        plt.title(
            "Realizations of Geometric Brownian Motion\n $dS_t = \mu S_t dt + \sigma S_t dW_t$\n $S_0 = {0}, \mu = {1}, \sigma = {2}$".format(self.S0, self.mu, self.sigma)
        )
        plt.show()

      if self.pandas == 'Y':
        output_St = pd.DataFrame(St)
      else:
        output_St = St

      return output_St

  def plot_paths(self, sim_df, FX_df, predicted_period, backtesting = False):

    """
    - Plots realizations of Geometric Brownian Motion along with actual exchange rates.

    - Parameters:
        - sim_df (Pandas DataFrame): Simulated GBM data.
        - FX_df (Pandas Series): Actual exchange rate data.
        - predicted_period (int): Number of predicted periods.
        - backtesting (bool): True for backtesting, False for regular simulation.
    """

    self.ticker = 'USD-Y'

    self.sim_df = sim_df
    self.FX_df = FX_df
    self.predicted_period = predicted_period
    self.backtesting = backtesting

    time_space = np.linspace(0,1,self.predicted_period+1)
    tt = np.full(shape=(10000, self.predicted_period + 1), fill_value=time_space).T
    tt_fx = np.full(shape=(1, self.predicted_period + 1), fill_value=time_space).T

    temp = self.FX_df[self.FX_df.index >= len(self.FX_df)-self.predicted_period-1].reset_index(drop = True)

    if self.backtesting == True:
      plot_df = self.sim_df
    else:
      df_nan = pd.DataFrame(np.nan, index=range(self.predicted_period), columns=range(len(self.sim_df.columns)))
      plot_df = pd.concat([df_nan, self.sim_df]).reset_index(drop = True)
      temp = pd.concat([temp, df_nan]).reset_index(drop = True)
      time_space = np.linspace(0,1,2*self.predicted_period+1)
      tt = np.full(shape=(10000, 2*self.predicted_period + 1), fill_value=time_space).T
      tt_fx = np.full(shape=(1, 2*self.predicted_period + 1), fill_value=time_space).T

    fig = plt.figure(figsize=(8,5))
    plt.plot(tt, plot_df)
    #plt.plot(tt_fx, temp)#, linewidth = 1, c = 'k')
    plt.xlabel("Years $(t)$")
    plt.ylabel("Exchange Rate $(S_t)$")
    plt.title(
            "Realizations of Geometric Brownian Motion of {3}\n $dS_t = \mu S_t dt + \sigma S_t dW_t$\n $S_0 = {0}, \mu = {1}, \sigma = {2}$".format(round(self.S0,6), round(self.mu,6), round(self.sigma,6), self.ticker)
        )
    plt.grid()
    plt.show()

  def plot_paths_on_profit_space(self, sim_df, FX_df, predicted_period, avg_returns, backtesting = False):

    """
    - Plots realizations of Geometric Brownian Motion with profit space boundaries.

    - Parameters:
        - sim_df (Pandas DataFrame): Simulated GBM data.
        - FX_df (Pandas Series): Actual exchange rate data.
        - predicted_period (int): Number of predicted periods.
        - avg_returns (float): Average returns for profit space boundaries.
        - backtesting (bool): True for backtesting, False for regular simulation.
    """

    t_start = 0
    t_end = 1
    t_step = 1/predicted_period

    avg_fee_rate = avg_returns

    profit_space = pd.DataFrame(columns=['t','bounds_x1', 'bounds_x2'])
    profit_space['t'] = pd.Series(np.arange(t_start-t_step,t_end,t_step))

    bounds_x1 = pd.Series(profitability_bounds(FX_df.iloc[-predicted_period-1], 0))
    bounds_x2 = pd.Series(profitability_bounds(FX_df.iloc[-predicted_period-1], 0))


    for i in range(1, len(profit_space)):
        bounds_x1 = pd.concat([bounds_x1, pd.Series(profitability_bounds(FX_df.iloc[-predicted_period-1], (((1+avg_fee_rate)**i)-1))[0])])
        bounds_x2 = pd.concat([bounds_x2, pd.Series(profitability_bounds(FX_df.iloc[-predicted_period-1], (((1+avg_fee_rate)**i)-1))[1])])

    profit_space['bounds_x1'] = bounds_x1.reset_index(drop=True)
    profit_space['bounds_x2'] = bounds_x2.reset_index(drop=True)

    self.ticker = 'USD-Y'

    self.sim_df = sim_df
    self.FX_df = FX_df
    self.predicted_period = predicted_period
    self.backtesting = backtesting

    time_space = np.linspace(0,1,self.predicted_period+1)
    tt = np.full(shape=(10000, self.predicted_period + 1), fill_value=time_space).T
    tt_fx = np.full(shape=(1, self.predicted_period + 1), fill_value=time_space).T

    temp = self.FX_df[self.FX_df.index >= len(self.FX_df)-self.predicted_period-1].reset_index(drop = True)

    if self.backtesting == True:
      plot_df = self.sim_df
    else:
      df_nan = pd.DataFrame(np.nan, index=range(self.predicted_period), columns=range(len(self.sim_df.columns)))
      plot_df = pd.concat([df_nan, self.sim_df]).reset_index(drop = True)
      temp = pd.concat([temp, df_nan]).reset_index(drop = True)
      time_space = np.linspace(0,1,2*self.predicted_period+1)
      tt = np.full(shape=(10000, 2*self.predicted_period + 1), fill_value=time_space).T
      tt_fx = np.full(shape=(1, 2*self.predicted_period + 1), fill_value=time_space).T

    fig = plt.figure(figsize=(8,5))
    plt.plot(tt, plot_df)
    #plt.plot(tt_fx, temp)#, linewidth = 1, c = 'k')
    x = profit_space['t']
    y1 = profit_space['bounds_x1']
    y2 = profit_space['bounds_x2']

    plt.fill_between(x, y1, y2, alpha=0.4)
    plt.xlabel("Years $(t)$")
    plt.ylabel("Exchange Rate $(S_t)$")
    plt.title(
            "Realizations of Geometric Brownian Motion of {3}\n $dS_t = \mu S_t dt + \sigma S_t dW_t$\n $S_0 = {0}, \mu = {1}, \sigma = {2}$".format(round(self.S0,6), round(self.mu,6), round(self.sigma,6), self.ticker)
        )
    plt.grid()
    plt.show()

  def pipeline(self, predicted_period, FX_data = pd.DataFrame(), ticker = '', start_date = [], end_date = [], interval = '', backtesting = True, plot_sim = False,):

    """
    - Executes the complete pipeline for Geometric Brownian Motion simulation and visualization.

    - Parameters:
        - predicted_period (int): Number of predicted periods.
        - FX_data (Pandas DataFrame, optional): Historical price data.
        - ticker (str): Ticker symbol.
        - start_date (list): Start date [year, month, day].
        - end_date (list/str): End date [year, month, day] or 'today'.
        - interval (str): Data interval (e.g., '1d').
        - backtesting (bool): True for backtesting, False for regular simulation.
        - plot_sim (bool): True to plot the simulation, False otherwise.
    """

    self.ticker = ticker
    self.start_date = start_date
    self.end_date = end_date
    self.interval = interval
    self.predicted_period = predicted_period
    self.backtesting = backtesting

    if FX_data.empty:
        self.FX_data = self.data_loading(ticker = self.ticker,
                            start_date=self.start_date,
                            end_date=self.end_date,
                            interval=self.interval)
    else:
        self.FX_data = FX_data

    self.returns = self.log_returnify(FX_data = self.FX_data,
                            date_col = 'Date')

    self.mu, self.sigma = self.GBM_params(self.returns['Adj Close'])

    self.sim = self.GBM(
        mu = self.mu*(self.predicted_period**(1/2)),
        sigma = self.sigma*(self.predicted_period**(1/2)),
        S0 = self.FX_data.at[len(self.FX_data)-self.predicted_period-1, 'Adj Close'] if backtesting == True else self.FX_data.at[len(self.FX_data)-1, 'Adj Close'],
        #FX_data.at[len(FX_data)-predicted_period-1, 'Close'],
        steps = self.predicted_period,
        n_paths = 1000)
    self.sim_df = self.sim

    if plot_sim:
        self.plot_paths(
            sim_df = self.sim,
            FX_df = self.FX_data['Adj Close'],
            predicted_period = self.predicted_period,
            backtesting = self.backtesting)

    self.streaks = self.streak_counter(self.returns)


In [5]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover

import ta

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


## Streak indicator

In [6]:
def streak_counter(data):
  direction_flag = data > data.shift(1)

  def f(x):
      x = x.diff().ne(0).cumsum()
      return x.groupby(x).cumcount()

  return pd.DataFrame(direction_flag).apply(f)

## Market beater search

In [7]:
def optimalization_func(series):
  return (abs(series['Return [%]']) / abs(series['Buy & Hold Return [%]']))

In [8]:
results_df = pd.DataFrame()

list_of_assets = ['%5EGDAXI', 'GBPUSD=X', 'EURUSD=X', 'USDJPY=X', '^NDX', '^GSPC']

for i in range(len(list_of_assets)):

  asset = list_of_assets[i]

  price = price_sim()

  FX_data = price.data_loading(ticker = asset, #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                      start_date=[2003,8,12],
                      end_date='today',
                      interval='1d',)

  returns = price.log_returnify(FX_data = FX_data,
                      date_col = 'Date')

  input_data = FX_data.copy()
  input_data = input_data.set_index('Date')
  input_data.index =pd.to_datetime(input_data.index)

  if sum(input_data['Volume'] == 0):
    input_data['Volume'] = 999

  if input_data.isna().any().any():
    input_data = input_data.dropna()

  class streak_eurusd(Strategy):

    close_streak = 2
    long_streak = 3
    short_streak = 3

    def init(self): #initian big calculations
      self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

    def next(self): #iterates through each candle
      if self.streak[-1] == self.close_streak:
        self.position.close()
      elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
        self.buy()
      elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
        self.sell()

  bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

  stats, heatmap = bt.optimize(
      close_streak = range(1,6,1),
      long_streak = range(1,6,1),
      short_streak = range(1,6,1),
      maximize = optimalization_func,
      #maximize = 'Win Rate [%]',
      return_heatmap = True
  )

  score = heatmap.sort_values().iloc[-6]
  close_param = heatmap.sort_values().iloc[-6:].index[0][0]
  long_streak_param = heatmap.sort_values().iloc[-6:].index[0][1]
  short_streak_param = heatmap.sort_values().iloc[-6:].index[0][2]

  results_df = pd.concat([results_df, pd.DataFrame({
      'asset': asset,
      'score': score,
      'close_param': close_param,
      'long_streak_param': long_streak_param,
      'short_streak_param': short_streak_param,
      '# Trades': stats['# Trades'],
      'Return [%]': stats['Return [%]'],
      'Buy & Hold Return [%]': stats['Buy & Hold Return [%]']}, index = [i])])

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [9]:
results_df

asset      score  close_param  long_streak_param  short_streak_param  \
0  %5EGDAXI   0.846798            5                  5                   3   
1  GBPUSD=X   2.784186            4                  3                   3   
2  EURUSD=X  11.116726            5                  3                   3   
3  USDJPY=X   3.971807            3                  2                   2   
4      ^NDX   0.747614            5                  4                   1   
5     ^GSPC   0.904100            5                  5                   2   

   # Trades   Return [%]  Buy & Hold Return [%]  
0        56   362.809217             428.448447  
1       198    71.128575             -25.547351  
2       140    94.258426              -8.478973  
3       376    95.203427              23.969804  
4        93  1013.997473            1356.312365  
5        54   381.136192             421.564112

## EURUSD strategy

In [10]:
price = price_sim()

FX_data = price.data_loading(ticker = 'EURUSD=X', #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                    start_date=[2003,8,12],
                    end_date='today',
                    interval='1d',)

returns = price.log_returnify(FX_data = FX_data,
                    date_col = 'Date')

input_data = FX_data.copy()
input_data = input_data.set_index('Date')
input_data.index =pd.to_datetime(input_data.index)

if sum(input_data['Volume'] == 0):
  input_data['Volume'] = 999

if input_data.isna().any().any():
  input_data = input_data.dropna()

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


In [11]:
class streak_eurusd(Strategy):

  """close_streak = 2
  long_streak = 4
  short_streak = 3
  buy - buy strategy"""

  close_streak = 2
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [12]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [13]:
stats, heatmap = bt.optimize(
    close_streak = range(1,6,1),
    long_streak = range(1,6,1),
    short_streak = range(1,6,1),
    maximize = optimalization_func,#'Return [%]',
    #maximize = 'Win Rate [%]',
    return_heatmap = True
)

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [14]:
heatmap.sort_values().iloc[-12:]

close_streak  long_streak  short_streak
1             2            3                5.586796
2             3            3                5.757403
5             3            4                6.677844
              2            1                9.738685
                           2                9.851304
                           3               10.515672
              3            3               11.116726
1             1            1                     NaN
2             2            2                     NaN
3             3            3                     NaN
4             4            4                     NaN
5             5            5                     NaN
dtype: float64

In [15]:
class streak_eurusd(Strategy):

  """close_streak = 2
  long_streak = 4
  short_streak = 3
  buy - buy strategy"""

  close_streak = 2
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [16]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [17]:
stats = bt.run()
stats

Start                     2003-12-01 00:00:00
End                       2024-03-13 00:00:00
Duration                   7408 days 00:00:00
Exposure Time [%]                   55.129179
Equity Final [$]               1488168.699263
Equity Peak [$]                1505359.191845
Return [%]                           48.81687
Buy & Hold Return [%]               -8.478973
Return (Ann.) [%]                    1.921372
Volatility (Ann.) [%]                9.419883
Sharpe Ratio                          0.20397
Sortino Ratio                        0.313399
Calmar Ratio                         0.077256
Max. Drawdown [%]                  -24.870051
Avg. Drawdown [%]                   -1.877802
Max. Drawdown Duration     3377 days 00:00:00
Avg. Drawdown Duration      133 days 00:00:00
# Trades                                  321
Win Rate [%]                         54.82866
Best Trade [%]                       6.683706
Worst Trade [%]                     -8.749881
Avg. Trade [%]                    

In [18]:
bt.plot()

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p1350', ...)

## GBPUSD strategy

In [19]:
price = price_sim()

FX_data = price.data_loading(ticker = 'GBPUSD=X', #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                    start_date=[2003,8,12],
                    end_date='today',
                    interval='1d',)

returns = price.log_returnify(FX_data = FX_data,
                    date_col = 'Date')

input_data = FX_data.copy()
input_data = input_data.set_index('Date')
input_data.index =pd.to_datetime(input_data.index)

if sum(input_data['Volume'] == 0):
  input_data['Volume'] = 999

if input_data.isna().any().any():
  input_data = input_data.dropna()

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


In [20]:
class streak_eurusd(Strategy):

  close_streak = 2
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [21]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [22]:
stats, heatmap = bt.optimize(
    close_streak = range(1,6,1),
    long_streak = range(1,6,1),
    short_streak = range(1,6,1),
    maximize = optimalization_func,#'Return [%]',
    #maximize = 'Win Rate [%]',
    return_heatmap = True
)

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [23]:
heatmap.sort_values().iloc[-12:]

close_streak  long_streak  short_streak
2             3            3               1.959795
5             3            4               1.968314
                           5               2.002676
3             1            1               2.165733
              4            4               2.346527
5             3            3               2.642206
4             3            3               2.785023
1             1            1                    NaN
2             2            2                    NaN
3             3            3                    NaN
4             4            4                    NaN
5             5            5                    NaN
dtype: float64

In [24]:

class streak_eurusd(Strategy):

  close_streak = 4
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [25]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [26]:
stats = bt.run()
stats

Start                     2003-12-01 00:00:00
End                       2024-03-13 00:00:00
Duration                   7408 days 00:00:00
Exposure Time [%]                    57.22138
Equity Final [$]               1711285.752065
Equity Peak [$]                1829957.315694
Return [%]                          71.128575
Buy & Hold Return [%]               -25.53967
Return (Ann.) [%]                    2.599275
Volatility (Ann.) [%]                 7.16143
Sharpe Ratio                         0.362955
Sortino Ratio                        0.561147
Calmar Ratio                         0.177996
Max. Drawdown [%]                  -14.603006
Avg. Drawdown [%]                   -1.980818
Max. Drawdown Duration     1596 days 00:00:00
Avg. Drawdown Duration       85 days 00:00:00
# Trades                                  198
Win Rate [%]                        56.565657
Best Trade [%]                      10.902773
Worst Trade [%]                     -9.468125
Avg. Trade [%]                    

In [27]:
bt.plot()

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p1730', ...)

## USDJPY strategy

In [28]:
price = price_sim()

FX_data = price.data_loading(ticker = 'USDJPY=X', #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                    start_date=[2003,8,12],
                    end_date='today',
                    interval='1d',)

returns = price.log_returnify(FX_data = FX_data,
                    date_col = 'Date')

input_data = FX_data.copy()
input_data = input_data.set_index('Date')
input_data.index =pd.to_datetime(input_data.index)

if sum(input_data['Volume'] == 0):
  input_data['Volume'] = 999

if input_data.isna().any().any():
  input_data = input_data.dropna()

/usr/local/lib/python3.10/dist-packages/pandas/core/internals/blocks.py:351: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


In [29]:
class streak_eurusd(Strategy):

  close_streak = 3
  long_streak = 2
  short_streak = 2

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    price = self.data.Close[-1]
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [30]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [31]:
stats, heatmap = bt.optimize(
    close_streak = range(1,6,1),
    long_streak = range(1,6,1),
    short_streak = range(1,6,1),
    maximize = optimalization_func, #'Return [%]',
    #maximize = 'Win Rate [%]',
    return_heatmap = True
)

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [32]:
heatmap.sort_values().iloc[-12:]

close_streak  long_streak  short_streak
3             1            4               1.889695
4             3            2               1.985270
3             4            2               2.043926
5             1            1               2.077219
4             4            2               2.099077
                           3               2.133886
3             2            2               3.970140
1             1            1                    NaN
2             2            2                    NaN
3             3            3                    NaN
4             4            4                    NaN
5             5            5                    NaN
dtype: float64

In [33]:
class streak_eurusd(Strategy):

  close_streak = 3
  long_streak = 2
  short_streak = 2

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    price = self.data.Close[-1]
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [34]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [35]:
stats = bt.run()
stats

Start                     2003-08-13 00:00:00
End                       2024-03-13 00:00:00
Duration                   7518 days 00:00:00
Exposure Time [%]                   59.528267
Equity Final [$]               1952034.269715
Equity Peak [$]                1952593.088836
Return [%]                          95.203427
Buy & Hold Return [%]               23.979866
Return (Ann.) [%]                      3.2056
Volatility (Ann.) [%]               10.045469
Sharpe Ratio                         0.319109
Sortino Ratio                        0.499511
Calmar Ratio                         0.154353
Max. Drawdown [%]                  -20.767969
Avg. Drawdown [%]                   -2.115212
Max. Drawdown Duration     1520 days 00:00:00
Avg. Drawdown Duration       87 days 00:00:00
# Trades                                  376
Win Rate [%]                        61.170213
Best Trade [%]                      13.246794
Worst Trade [%]                     -6.633677
Avg. Trade [%]                    

In [36]:
bt.plot()

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p2110', ...)

## SP500 strategy

In [37]:
price = price_sim()

FX_data = price.data_loading(ticker = '^GSPC', #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                    start_date=[2003,8,12],
                    end_date='today',
                    interval='1d',)

returns = price.log_returnify(FX_data = FX_data,
                    date_col = 'Date')

input_data = FX_data.copy()
input_data = input_data.set_index('Date')
input_data.index =pd.to_datetime(input_data.index)

if sum(input_data['Volume'] == 0):
  input_data['Volume'] = 999

if input_data.isna().any().any():
  input_data = input_data.dropna()

In [38]:
class streak_eurusd(Strategy):

  close_streak = 2
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [39]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [40]:
stats, heatmap = bt.optimize(
    close_streak = range(1,6,1),
    long_streak = range(1,6,1),
    short_streak = range(1,6,1),
    maximize = optimalization_func, #'Return [%]',
    #maximize = 'Win Rate [%]',
    return_heatmap = True
)

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [41]:
heatmap.sort_values().iloc[-12:]

close_streak  long_streak  short_streak
5             4            3               0.461936
4             4            1               0.530408
5             4            1               0.539964
                           2               0.543382
              3            3               0.850765
              5            1               0.888913
                           2               0.904100
1             1            1                    NaN
2             2            2                    NaN
3             3            3                    NaN
4             4            4                    NaN
5             5            5                    NaN
dtype: float64

In [42]:
class streak_eurusd(Strategy):

  close_streak = 5
  long_streak = 5
  short_streak = 2

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [43]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [44]:
stats = bt.run()
stats

Start                     2003-08-12 00:00:00
End                       2024-03-13 00:00:00
Duration                   7519 days 00:00:00
Exposure Time [%]                   81.802393
Equity Final [$]               4811361.924219
Equity Peak [$]                5112645.095695
Return [%]                         381.136192
Buy & Hold Return [%]              421.564112
Return (Ann.) [%]                    7.939054
Volatility (Ann.) [%]                18.32281
Sharpe Ratio                         0.433288
Sortino Ratio                        0.658228
Calmar Ratio                         0.162464
Max. Drawdown [%]                  -48.866516
Avg. Drawdown [%]                   -2.205927
Max. Drawdown Duration     1193 days 00:00:00
Avg. Drawdown Duration       32 days 00:00:00
# Trades                                   54
Win Rate [%]                        75.925926
Best Trade [%]                      47.341578
Worst Trade [%]                    -33.694682
Avg. Trade [%]                    

In [45]:
bt.plot()

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p2490', ...)

## Nasdaq100 strategy

In [46]:
price = price_sim()

FX_data = price.data_loading(ticker = '^NDX', #'^NDX', #'NQ%3DF',   #'^GSPC', #EURUSD=X
                    start_date=[2003,8,12],
                    end_date='today',
                    interval='1d',)

returns = price.log_returnify(FX_data = FX_data,
                    date_col = 'Date')

input_data = FX_data.copy()
input_data = input_data.set_index('Date')
input_data.index =pd.to_datetime(input_data.index)

if sum(input_data['Volume'] == 0):
  input_data['Volume'] = 999

if input_data.isna().any().any():
  input_data = input_data.dropna()

In [47]:
class streak_eurusd(Strategy):

  close_streak = 2
  long_streak = 3
  short_streak = 3

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [48]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [49]:
stats, heatmap = bt.optimize(
    close_streak = range(1,6,1),
    long_streak = range(1,6,1),
    short_streak = range(1,6,1),
    maximize = optimalization_func,
    #maximize = 'Win Rate [%]',
    return_heatmap = True
)

Backtest.optimize:   0%|          | 0/3 [00:00<?, ?it/s]

In [50]:
heatmap.sort_values().iloc[-12:]

close_streak  long_streak  short_streak
4             3            1               0.365338
5             3            1               0.401715
4             4            2               0.412163
5             5            2               0.491404
4             4            1               0.601677
5             5            1               0.734386
              4            1               0.747614
1             1            1                    NaN
2             2            2                    NaN
3             3            3                    NaN
4             4            4                    NaN
5             5            5                    NaN
dtype: float64

In [51]:
class streak_eurusd(Strategy):

  close_streak = 5
  long_streak = 4
  short_streak = 1

  def init(self): #initian big calculations
    self.streak = self.I(streak_counter, pd.Series(self.data.Close),)

  def next(self): #iterates through each candle
    if self.streak[-1] == self.close_streak:
      self.position.close()
    elif (self.streak[-1] == self.short_streak) and (self.data.Close[-1] < self.data.Close[-2]):
      self.buy()
    elif (self.streak[-1] == self.long_streak) and (self.data.Close[-1] > self.data.Close[-2]):
      self.sell()


In [52]:
bt = Backtest(input_data, streak_eurusd, cash = 1_000_000)

In [53]:
stats = bt.run()
stats

Start                     2003-08-12 00:00:00
End                       2024-03-13 00:00:00
Duration                   7519 days 00:00:00
Exposure Time [%]                   90.659977
Equity Final [$]              11139974.727034
Equity Peak [$]                 12020957.3603
Return [%]                        1013.997473
Buy & Hold Return [%]             1356.312365
Return (Ann.) [%]                   12.437154
Volatility (Ann.) [%]               24.103982
Sharpe Ratio                         0.515979
Sortino Ratio                        0.834735
Calmar Ratio                         0.250309
Max. Drawdown [%]                  -49.687244
Avg. Drawdown [%]                   -2.867746
Max. Drawdown Duration     1091 days 00:00:00
Avg. Drawdown Duration       34 days 00:00:00
# Trades                                   93
Win Rate [%]                        70.967742
Best Trade [%]                      34.396801
Worst Trade [%]                    -34.844487
Avg. Trade [%]                    

In [54]:
bt.plot()

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p2868', ...)

## Market beater search
- based on invetigation, EURUSD params are proposed to change to 2,3,3 instread of 5,3,3

In [55]:
results_adj_df = results_df.copy()

new_row = pd.DataFrame({
      'asset': 'EURUSD=X',
      'score': 5.757403,
      'close_param': 2,
      'long_streak_param': 3,
      'short_streak_param': 3,
      '# Trades': 321,
      'Return [%]': 48.81687,
      'Buy & Hold Return [%]': -8.478973}, index = [2])

results_adj_df.iloc[2,:] = new_row
results_adj_df

asset     score  close_param  long_streak_param  short_streak_param  \
0    %5EGDAXI  0.846798            5                  5                   3   
1    GBPUSD=X  2.784186            4                  3                   3   
2  [EURUSD=X]  5.757403            2                  3                   3   
3    USDJPY=X  3.971807            3                  2                   2   
4        ^NDX  0.747614            5                  4                   1   
5       ^GSPC  0.904100            5                  5                   2   

   # Trades   Return [%]  Buy & Hold Return [%]  
0        56   362.809217             428.448447  
1       198    71.128575             -25.547351  
2       321    48.816870              -8.478973  
3       376    95.203427              23.969804  
4        93  1013.997473            1356.312365  
5        54   381.136192             421.564112